In [1]:
import pandas as pd
import requests
import json
import datetime as dt
import os
import plotly as plt
import tensorflow as tf
import keras
import numpy as np
import pyod
from pyod.models.ecod import ECOD
import time
import plotly.express as px

# Generation Data

Os dados estão na pasta data/loandas/generation_data. Os dados foram particionados em json.

In [3]:
json_file_path = 'C:/Users/EMC/Documents/doutorado/doctorade/data/loanda/generation_data/'

os.listdir(json_file_path)

['loanda_data_curated_0.json',
 'loanda_data_curated_200000.json',
 'loanda_data_curated_400000.json',
 'loanda_data_curated_600000.json',
 'loanda_data_curated_800000.json']

Data cleaning was conducted by removing null records indicating periods when production had not yet commenced. For each production batch, the variable yX was created to represent production per minute. This variable was derived from the Daily Energy variable, which records the cumulative total of generated energy. The purpose of this approach is to ensure a more accurate and detailed representation of production per batch by eliminating irrelevant or non-applicable data during periods when actual production was not taking place. The column names were translated from Portuguese to English

In [7]:
json_file_path = 'C:/Users/EMC/Documents/doutorado/doctorade/data/loanda/generation_data/'
df_generation = pd.DataFrame()
for data_chunks in os.listdir(json_file_path):
    path = json_file_path + data_chunks
    with open(path, "r") as json_file:
    # Load the JSON data into a Python object.
        json_data = json.load(json_file)
        pd_json_data = pd.DataFrame.from_dict(json_data)
        df_generation = pd.concat([df_generation,pd_json_data])

df = df_generation
# Find None
df = df.replace('nan', None)
# To Datetime
df['E3TimeStamp'] = pd.to_datetime(df['E3TimeStamp'], format = 'mixed')

df_time = df['E3TimeStamp']

df_float = df[['PotenciaAtivaTotal', 'EnergiaTotal_DataLogger',
       'EnergiaDiaria_DataLogger', 'RadiacaoGlobal', 'TempAr', 'TempModulo',
       'VelocidadeVento', 'EnergiaTotal_LoteB', 'EnergiaDiaria_LoteB',
       'EnergiaReativa_LoteB', 'EnergiaTotal_LoteC', 'EnergiaDiaria_LoteC',
       'EnergiaReativa_LoteC', 'EnergiaTotal_LoteD', 'EnergiaDiaria_LoteD',
       'EnergiaReativa_LoteD', 'EnergiaTotal_LoteE', 'EnergiaDiaria_LoteE',
       'EnergiaReativa_LoteE', 'EnergiaTotal_LoteF', 'EnergiaDiaria_LoteF',
       'EnergiaReativa_LoteF']].astype(float)

df = pd.concat([df_time,df_float], axis = 1)

df = df.sort_values(by='E3TimeStamp')

# Criar geração por minuto
try:
    df = df.set_index('E3TimeStamp')
except:
    pass

# Diferenças negativas
df['yB'] = df.EnergiaDiaria_LoteB.diff().shift(-1)
df['yC'] = df.EnergiaDiaria_LoteC.diff().shift(-1)
df['yD'] = df.EnergiaDiaria_LoteD.diff().shift(-1)
df['yE'] = df.EnergiaDiaria_LoteE.diff().shift(-1)
df['yF'] = df.EnergiaDiaria_LoteF.diff().shift(-1)

# Traduzir colunas
df.columns = ['ActivePowerTotal', 'TotalEnergy_DataLogger',
              'DailyEnergy_DataLogger', 'GlobalRadiation', 'AirTemperature', 'ModuleTemperature',
              'WindSpeed', 'TotalEnergy_B', 'DailyEnergy_B',
              'ReactiveEnergy_B', 'TotalEnergy_C', 'DailyEnergy_C',
              'ReactiveEnergy_C', 'TotalEnergy_D', 'DailyEnergy_D',
              'ReactiveEnergy_D', 'TotalEnergy_E', 'DailyEnergy_E',
              'ReactiveEnergy_E', 'TotalEnergy_F', 'DailyEnergy_F',
              'ReactiveEnergy_F', 'yB', 'yC', 'yD', 'yE', 'yF']
# Excluir valores nulos pelo Lote F onde temos o início mais tardio.

df = df[~(df['yF'].isna())]

# EDA

In [9]:
df.isna().sum()

ActivePowerTotal          0
TotalEnergy_DataLogger    0
DailyEnergy_DataLogger    0
GlobalRadiation           0
AirTemperature            0
ModuleTemperature         0
WindSpeed                 0
TotalEnergy_B             0
DailyEnergy_B             0
ReactiveEnergy_B          0
TotalEnergy_C             0
DailyEnergy_C             0
ReactiveEnergy_C          0
TotalEnergy_D             0
DailyEnergy_D             0
ReactiveEnergy_D          0
TotalEnergy_E             0
DailyEnergy_E             0
ReactiveEnergy_E          0
TotalEnergy_F             0
DailyEnergy_F             0
ReactiveEnergy_F          0
yB                        0
yC                        0
yD                        0
yE                        0
yF                        0
dtype: int64

In [10]:
try:
  df = df.set_index('E3TimeStamp')
except:
  pass
try:
  del df['time_join_generation']
except:
  pass
try:
  del df['time_in_iso8601']
except:
  pass


df_descricao = pd.DataFrame()

df_descricao['No_None_Values_Count'] = round(df.apply(lambda x: x.count()),2)
df_descricao['None_Values_Count'] = round(df.apply(lambda x: x.isnull().sum()),2)
df_descricao['Zeroes_Values_Count'] = round(df.apply(lambda x: (x == 0).sum()),2)
df_descricao['Min_Values'] = round(df.apply(lambda x: x.min()),2)
df_descricao['Max_Values'] = round(df.apply(lambda x: x.max()),2)
df_descricao['Mean_Values'] = round(df.apply(lambda x: x.mean()),2)
df_descricao['Std_Values'] = round(df.apply(lambda x: x.std()),2)
df_descricao['Sum of Values'] = round(df.apply(lambda x: x.sum()),0)
df_descricao['Min_Date'] = df.index.min()
df_descricao['Max_Date'] = df.index.max()
df_descricao

No_None_Values_Count  None_Values_Count   
ActivePowerTotal                      772953                  0  \
TotalEnergy_DataLogger                772953                  0   
DailyEnergy_DataLogger                772953                  0   
GlobalRadiation                       772953                  0   
AirTemperature                        772953                  0   
ModuleTemperature                     772953                  0   
WindSpeed                             772953                  0   
TotalEnergy_B                         772953                  0   
DailyEnergy_B                         772953                  0   
ReactiveEnergy_B                      772953                  0   
TotalEnergy_C                         772953                  0   
DailyEnergy_C                         772953                  0   
ReactiveEnergy_C                      772953                  0   
TotalEnergy_D                         772953                  0   
DailyEnergy_D                         772953                  0   
ReactiveEnergy_D                      772953                  0   
TotalEnergy_E                         772953                  0   
DailyEnergy_E                         772953                  0   
ReactiveEnergy_E                      772953                  0   
TotalEnergy_F                         772953                  0   
DailyEnergy_F                         772953                  0   
ReactiveEnergy_F                      772953                  0   
yB                                    772953                  0   
yC                                    772953                  0   
yD                                    772953                  0   
yE                                    772953                  0   
yF                                    772953                  0   

                        Zeroes_Values_Count  Min_Values   Max_Values   
ActivePowerTotal                     396181        0.00      5040.00  \
TotalEnergy_DataLogger               107847        0.00  18560752.00   
DailyEnergy_DataLogger               208800        0.00     43244.00   
GlobalRadiation                       33797      -20.00      1650.00   
AirTemperature                         6502        0.00       195.00   
ModuleTemperature                      6502        0.00       197.00   
WindSpeed                            145677      -10.00        58.00   
TotalEnergy_B                         18191        0.00   4325685.60   
DailyEnergy_B                        128272        0.00      8635.40   
ReactiveEnergy_B                     386054      -60.06        41.35   
TotalEnergy_C                         26438        0.00   4098646.00   
DailyEnergy_C                        132768        0.00      8636.80   
ReactiveEnergy_C                     386430      -44.16        36.57   
TotalEnergy_D                         71448        0.00   3384084.00   
DailyEnergy_D                        167492        0.00      8661.70   
ReactiveEnergy_D                     412483      -42.79        42.10   
TotalEnergy_E                         20432        0.00   3382267.20   
DailyEnergy_E                        125802        0.00      8705.40   
ReactiveEnergy_E                     382436      -59.43        42.48   
TotalEnergy_F                         21500        0.00   3376782.40   
DailyEnergy_F                        126782        0.00      8642.10   
ReactiveEnergy_F                     390152      -56.94        42.58   
yB                                   428786    -8632.20      8027.30   
yC                                   434853    -8636.80      8334.30   
yD                                   447550    -8661.70      8338.80   
yE                                   428434    -8705.40      8170.80   
yF                                   422654    -8642.10      7689.60   

                        Mean_Values  Std_Values  Sum of Values   
ActivePowerTotal            1128.28     1670.66   8.721067e+08  

In [13]:
# Correlation
df_corr = df[['GlobalRadiation', 'AirTemperature', 'ModuleTemperature',
       'WindSpeed', 'yB', 'yC', 'yD', 'yE', 'yF','DailyEnergy_B','DailyEnergy_C','DailyEnergy_D','DailyEnergy_E','DailyEnergy_F']].corr().round(2)
fig = px.imshow(df_corr, text_auto=True, aspect="auto")
fig.show()

# Identify Anomaly type and visualize data

Point Anomaly:<br>
A point anomaly is defined as a single data point that is unusual compared to the rest of the data. A single balmy day in an otherwise chilly winter would be a good example of this.
On that day, the weather is considered anomalous because the temperature is extreme compared to the rest of the season. Point anomalies often occur in this way, as a singular extreme value on a single attribute of the data.

Contextual Anomaly:<br>
Also called conditional outliers, contextual anomalies contain data points that significantly deviate from the other data points that exist in the same context. An anomaly in the context of one dataset may not be an anomaly in another.
For instance, one of your customers may double their usual spending behavior in mid-December for the holiday season. These outliers are common in time series data because those datasets are records of specific quantities for given periods.

Collective anomaly:<br>
A collective anomaly is a collection of similar data points that can be considered abnormal together when compared to the rest of the data.
For example, a consecutive 10-day period of hot temperatures could be considered a collective anomaly.
These temperatures are unusual because they occur together and are likely caused by the same underlying weather event.

## Point Anomaly

### Daily Energy

The Daily Energy variable is designed to exhibit a consistent daily growth pattern. It starts with an initial value of 0 and experiences continuous minute-by-minute energy generation throughout the day, reaching its peak before resetting to 0 at the day's end. A visual representation of this behavior in the plot highlights an anomaly in the data, particularly during the midday period. During this timeframe, the data logger records values of Daily Energy (t) that are lower than the preceding timestamp (t-1), suggesting a potential anomaly stemming from either the data logger itself or the underlying database.

In [14]:
df_periodo = df[(df.index >= '2022-05-12') & (df.index < '2022-05-16')]
plt.plot(x = df_periodo.index,y= [df_periodo['DailyEnergy_B'],df_periodo['DailyEnergy_C'],df_periodo['DailyEnergy_D'],df_periodo['DailyEnergy_F']], data_frame=df_periodo, kind='line')

### yX
The variable yX is derived from the daily energy measurement, representing the energy production per minute. Within the time series, we can identify point anomalies, with instances where the values turn negative serving as indicators of potential issues in the data logger associated with the Daily Energy information.

In [21]:
df_periodo = df[(df.index >= '2022-05-12') & (df.index < '2022-05-16')]
plt.plot(x = df_periodo.index,y= [df_periodo['yB'],df_periodo['yC'],df_periodo['yD'],df_periodo['yF']], data_frame=df_periodo, kind='line')

### Global Radiation
Examine anomalies in global radiation, particularly sudden drops throughout the day and isolated zero values. These significant variations may indicate potential issues in the measurement system or data acquisition, necessitating a more in-depth investigation to ensure the accuracy and reliability of global radiation information.

In [15]:
df_periodo = df[(df.index >= '2022-08-09') & (df.index < '2022-08-18')]
plt.plot(x = df_periodo.index,y= [df_periodo['GlobalRadiation']], data_frame=df_periodo, kind='line')

## Collective Anomaly

### Air Temperature and Module Temperature
Examine anomalous readings in the air temperature and tempModulo data logger, specifically focusing on maximum temperatures reaching 195 degrees observed in the EDA section. Notably, there are extremely high temperatures recorded during nighttime periods, suggesting potential anomalies that warrant investigation.

In [16]:
df[df.AirTemperature > 50.0]

ActivePowerTotal  TotalEnergy_DataLogger   
E3TimeStamp                                                         
2022-05-18 14:44:48.840            3452.0               6631063.0  \
2022-05-18 14:46:48.763            2319.0               6631114.0   
2022-05-18 14:47:48.780            1078.0               6631146.0   
2022-05-18 14:48:48.773            3278.0               6631176.0   
2022-05-18 14:49:48.750            3741.0               6631235.0   
...                                   ...                     ...   
2022-05-19 11:15:48.753            2030.0               6642257.0   
2022-05-19 11:16:48.757            2199.0               6642292.0   
2022-05-19 11:28:48.847            2265.0               6642782.0   
2022-05-19 11:32:49.043            1974.0               6642922.0   
2022-05-19 12:20:48.830            5040.0               6645402.0   

                         DailyEnergy_DataLogger  GlobalRadiation   
E3TimeStamp                                                        
2022-05-18 14:44:48.840                 10552.0            308.0  \
2022-05-18 14:46:48.763                 10603.0            428.0   
2022-05-18 14:47:48.780                 10635.0            160.0   
2022-05-18 14:48:48.773                 10665.0            465.0   
2022-05-18 14:49:48.750                 10724.0            621.0   
...                                         ...              ...   
2022-05-19 11:15:48.753                  7720.0            252.0   
2022-05-19 11:16:48.757                  7755.0            274.0   
2022-05-19 11:28:48.847                  8245.0            277.0   
2022-05-19 11:32:49.043                  8384.0            273.0   
2022-05-19 12:20:48.830                 10864.0            708.0   

                         AirTemperature  ModuleTemperature  WindSpeed   
E3TimeStamp                                                             
2022-05-18 14:44:48.840            54.0               67.0      -10.0  \
2022-05-18 14:46:48.763            60.0               73.0      -10.0   
2022-05-18 14:47:48.780            62.0               75.0      -10.0   
2022-05-18 14:48:48.773            74.0               87.0      -10.0   
2022-05-18 14:49:48.750            70.0               83.0      -10.0   
...                                 ...                ...        ...   
2022-05-19 11:15:48.753            91.0              102.0      -10.0   
2022-05-19 11:16:48.757            91.0              103.0      -10.0   
2022-05-19 11:28:48.847            54.0               69.0      -10.0   
2022-05-19 11:32:49.043            51.0               67.0      -10.0   
2022-05-19 12:20:48.830            55.0               80.0      -10.0   

                         TotalEnergy_B  DailyEnergy_B  ReactiveEnergy_B  ...   
E3TimeStamp                                                              ...   
2022-05-18 14:44:48.840      1925344.1         2585.4            -6.751  ...  \
2022-05-18 14:46:48.763      1925356.3         2597.4            -0.503  ...   
2022-05-18 14:47:48.780      1925365.3         2606.4            -1.382  ...   
2022-05-18 14:48:48.773      1925371.2         2612.2            -4.231  ...   
2022-05-18 14:49:48.750      1925384.7         2626.4             9.090  ...   
...                                ...            ...               ...  ...   
2022-05-19 11:15:48.753      1927639.7         1519.2             5.257  ...   
2022-05-19 11:16:48.757      1927646.4         1526.0             6.616  ...   
2022-05-19 11:28:48.847      1927745.3         1624.9             5.308  ...   
2022-05-19 11:32:49.043      1927774.7         1654.1            -1.169  ...   
2022-05-19 12:20:48.830      1928287.8         2166.9            10.017  ...   

                         DailyEnergy_E  ReactiveEnergy_E  TotalEnergy_F   
E3TimeStamp                                                               
2022-05-18 14:44:48.840         2618.2            -4.561       947117.3  \
2022-05-18 14:46:48.763   

In [17]:
df_periodo = df[(df.index >= '2022-05-18') & (df.index < '2022-05-22')]
plt.plot(x = df_periodo.index,y= [df_periodo['AirTemperature'],df_periodo['ModuleTemperature']], data_frame=df_periodo, kind='line')

### Wind Speed
Anomalies in wind speed readings, especially when they remain consistently at -10, can be indicative of measurement errors, instrument malfunction, or data transmission issues. Wind speed is typically measured in positive values, and sustained negative readings are not physically meaningful in the context of standard wind speed measurements.

In [18]:
df[df.WindSpeed < 0]

ActivePowerTotal  TotalEnergy_DataLogger   
E3TimeStamp                                                         
2022-03-22 10:59:55.207            3909.0               4416209.0  \
2022-03-22 11:00:55.303            4032.0               4416274.0   
2022-03-22 11:01:55.207            4032.0               4416341.0   
2022-03-22 11:02:55.177            4032.0               4416409.0   
2022-03-22 11:03:55.187            4032.0               4416476.0   
...                                   ...                     ...   
2022-05-26 14:51:48.810            3308.0               6882336.0   
2022-05-26 14:52:48.950            2504.0               6882384.0   
2022-05-26 14:53:48.850            1988.0               6882420.0   
2022-05-26 14:54:48.817            2247.0               6882453.0   
2022-05-26 14:55:48.770            2573.0               6882494.0   

                         DailyEnergy_DataLogger  GlobalRadiation   
E3TimeStamp                                                        
2022-03-22 10:59:55.207                 10655.0            871.0  \
2022-03-22 11:00:55.303                 10720.0            893.0   
2022-03-22 11:01:55.207                 10786.0            940.0   
2022-03-22 11:02:55.177                 10854.0           1062.0   
2022-03-22 11:03:55.187                 10921.0           1056.0   
...                                         ...              ...   
2022-05-26 14:51:48.810                 22009.0            511.0   
2022-05-26 14:52:48.950                 22057.0            396.0   
2022-05-26 14:53:48.850                 22092.0            325.0   
2022-05-26 14:54:48.817                 22126.0            351.0   
2022-05-26 14:55:48.770                 22166.0            375.0   

                         AirTemperature  ModuleTemperature  WindSpeed   
E3TimeStamp                                                             
2022-03-22 10:59:55.207            28.0               46.0      -10.0  \
2022-03-22 11:00:55.303            28.0               46.0      -10.0   
2022-03-22 11:01:55.207            28.0               46.0      -10.0   
2022-03-22 11:02:55.177            28.0               46.0      -10.0   
2022-03-22 11:03:55.187            28.0               46.0      -10.0   
...                                 ...                ...        ...   
2022-05-26 14:51:48.810            28.0               39.0      -10.0   
2022-05-26 14:52:48.950            28.0               39.0      -10.0   
2022-05-26 14:53:48.850            28.0               39.0      -10.0   
2022-05-26 14:54:48.817            27.0               38.0      -10.0   
2022-05-26 14:55:48.770            27.0               38.0      -10.0   

                         TotalEnergy_B  DailyEnergy_B  ReactiveEnergy_B  ...   
E3TimeStamp                                                              ...   
2022-03-22 10:59:55.207      1613070.1         2672.3             7.435  ...  \
2022-03-22 11:00:55.303      1613085.5         2688.2             7.695  ...   
2022-03-22 11:01:55.207      1613103.7         2705.5             8.952  ...   
2022-03-22 11:02:55.177      1613119.9         2721.9             2.078  ...   
2022-03-22 11:03:55.187      1613136.2         2738.5            -4.827  ...   
...                                ...            ...               ...  ...   
2022-05-26 14:51:48.810      1975152.8         4375.5             5.748  ...   
2022-05-26 14:52:48.950      1975162.7         4385.5            -3.950  ...   
2022-05-26 14:53:48.850      1975169.3         4391.6            -0.722  ...   
2022-05-26 14:54:48.817      1975176.4         4399.0             4.424  ...   
2022-05-26 14:55:48.770      1975183.8         4406.2             4.293  ...   

                         DailyEnergy_E  ReactiveEnergy_E  TotalEnergy_F   
E3TimeStamp                                                               
2022-03-22 10:59:55.207         2662.4             6.417       648579.3  \
2022-03-22 11:00:55.303   

In [19]:
df_periodo = df[(df.index >= '2022-03-21') & (df.index < '2022-03-25')]
plt.plot(x = df_periodo.index,y= [df_periodo['WindSpeed']], data_frame=df_periodo, kind='line')

# Anomaly detection

## PYOD Unsupervised Outlier Detection Using Empirical Cumulative Distribution Functions <br>

In [183]:
start_time = time.time()

df_anomaly = df[['yB', 'yC', 'yD', 'yE', 'yF','VelocidadeVento','TempModulo','TempAr','RadiacaoGlobal']].copy()

train_row_number = 80000

for y in df_anomaly.columns:
    df_y = df_anomaly[[y]]

    # Normalize and save the mean and std we get,
    # for normalizing test data.
    training_mean = df_y.mean()
    training_std = df_y.std()
    df_y_normalized = (df_y - training_mean) / training_std

    train = df_y_normalized.iloc[:train_row_number,:]
    test = df_y_normalized.iloc[train_row_number:,:]

    clf = ECOD()
    clf.fit(train)

    # get outlier scores
    y_train_scores = clf.decision_scores_  # raw outlier scores on the train data
    y_test_scores = clf.decision_function(test)  # predict raw outlier scores on test

    # The threshold is 6 times the standard deviation
    results_ecod_test = df_y[[y]].iloc[train_row_number:,:][(y_test_scores > y_test_scores.std()*6)]
    results_ecod_training = df_y[[y]].iloc[:train_row_number,:][(y_train_scores > y_train_scores.std()*6)]

    total_anomalias = df_anomaly.loc[pd.concat([results_ecod_test,results_ecod_training]).index,:]

    df_y.loc[total_anomalias.index,:] = None
    df_anomaly[str(y) + '_anomalia'] = False
    df_anomaly.loc[total_anomalias.index,str(y) + '_anomalia'] = True

    df_anomaly[y] = df_y[y].interpolate()

end_time = time.time()

# Resultado ECOD:
ecod_results = pd.DataFrame(df_anomaly[['yB_anomalia', 'yC_anomalia', 'yD_anomalia',
   'yE_anomalia', 'yF_anomalia', 'VelocidadeVento_anomalia',
   'TempModulo_anomalia', 'TempAr_anomalia',
   'RadiacaoGlobal_anomalia']].sum()/len(df_anomaly) * 100, columns = ["% of anomaly"])
ecod_results.loc['algoritmo_anomalia',:] = 'PyOD - ECOD'
ecod_results.loc['tempo_execucao (s)',:] = end_time - start_time
ecod_results.loc['threshold',:] = "6x scores std"
ecod_results.loc['% of traning samples',:] = len(train)/len(df_anomaly)*100

## Resultado ECOD
- % Anomalia<br>
- Verificação dos valores máximos e mínimos
- Correlação entre variáveis
- Threshold utilizado

In [185]:
ecod_results

% of anomaly
yB_anomalia                    0.525776
yC_anomalia                    0.509087
yD_anomalia                    0.473379
yE_anomalia                    0.546864
yF_anomalia                    0.504688
VelocidadeVento_anomalia       0.475449
TempModulo_anomalia            0.250339
TempAr_anomalia                0.251891
RadiacaoGlobal_anomalia         0.59111
algoritmo_anomalia          PyOD - ECOD
tempo_execucao (s)             2.694521
threshold                 6x scores std
% of traning samples          10.349918

In [72]:
try:
  df = df.set_index('E3TimeStamp')
except:
  pass


df_filtered = df_anomaly[['RadiacaoGlobal', 'TempAr', 'TempModulo',
       'VelocidadeVento', 'yB', 'yC', 'yD', 'yE', 'yF']]

df_descricao = pd.DataFrame()

df_descricao['No_None_Values_Count'] = round(df_filtered.apply(lambda x: x.count()),2)
df_descricao['None_Values_Count'] = round(df_filtered.apply(lambda x: x.isnull().sum()),2)
df_descricao['Zeroes_Values_Count'] = round(df_filtered.apply(lambda x: (x == 0).sum()),2)
df_descricao['Min_Values'] = round(df_filtered.apply(lambda x: x.min()),2)
df_descricao['Max_Values'] = round(df_filtered.apply(lambda x: x.max()),2)
df_descricao['Mean_Values'] = round(df_filtered.apply(lambda x: x.mean()),2)
df_descricao['Std_Values'] = round(df_filtered.apply(lambda x: x.std()),2)
df_descricao['Sum of Values'] = round(df_filtered.apply(lambda x: x.sum()),0)
df_descricao['Min_Date'] = df_filtered.index.min()
df_descricao['Max_Date'] = df_filtered.index.max()
df_descricao

No_None_Values_Count  None_Values_Count  Zeroes_Values_Count   
RadiacaoGlobal                 772953                  0                33797  \
TempAr                         772953                  0                 6502   
TempModulo                     772953                  0                 6517   
VelocidadeVento                772953                  0               145683   
yB                             772953                  0               429956   
yC                             772953                  0               436247   
yD                             772953                  0               448630   
yE                             772953                  0               429668   
yF                             772953                  0               423469   

                 Min_Values  Max_Values  Mean_Values  Std_Values   
RadiacaoGlobal        -13.0      1324.0       214.70      318.62  \
TempAr                  0.0        39.0        23.38        5.88   
TempModulo              0.0        69.0        27.63       13.67   
VelocidadeVento       -10.0         6.0         0.48        4.14   
yB                      0.0        26.1         3.84        5.78   
yC                      0.0        34.6         3.74        5.70   
yD                      0.0        18.6         3.53        5.58   
yE                      0.0        17.2         3.79        5.71   
yF                      0.0        17.2         3.88        5.79   

                 Sum of Values                Min_Date                Max_Date  
RadiacaoGlobal     165952794.0 2021-12-09 10:36:17.677 2023-08-09 22:19:10.373  
TempAr              18073734.0 2021-12-09 10:36:17.677 2023-08-09 22:19:10.373  
TempModulo          21357582.0 2021-12-09 10:36:17.677 2023-08-09 22:19:10.373  
VelocidadeVento       374234.0 2021-12-09 10:36:17.677 2023-08-09 22:19:10.373  
yB                   2971977.0 2021-12-09 10:36:17.677 2023-08-09 22:19:10.373  
yC                   2889621.0 2021-12-09 10:36:17.677 2023-08-09 22:19:10.373  
yD                   2730929.0 2021-12-09 10:36:17.677 2023-08-09 22:19:10.373  
yE                   2927693.0 2021-12-09 10:36:17.677 2023-08-09 22:19:10.373  
yF                   2997650.0 2021-12-09 10:36:17.677 2023-08-09 22:19:10.373

In [86]:
df_corr = df_filtered.corr()

fig = px.imshow(df_corr, text_auto=True, aspect="auto")
fig.show()

# Criar granularidade de HORA

In [93]:
df_hora_soma = df_filtered[['yB','yC', 'yD', 'yE', 'yF']]
df_hora_soma = df_hora_soma.resample('H').sum()
df_hora_soma

yB           yC           yD   yE   yF
E3TimeStamp                                                         
2021-12-09 10:00:00     0.000000     0.000000     0.000000  0.0  0.0
2021-12-09 11:00:00   496.200000   486.650000   395.000000  0.0  0.0
2021-12-09 12:00:00    70.000000    71.800000    71.000000  0.0  0.0
2021-12-09 13:00:00    19.000000    86.000000    89.000000  0.0  0.0
2021-12-09 14:00:00  1433.030928  1540.227835  1601.291753  0.0  0.0
...                          ...          ...          ...  ...  ...
2023-08-09 18:00:00     2.100000     2.200000     2.300000  2.2  2.4
2023-08-09 19:00:00     0.000000     0.000000     0.000000  0.0  0.0
2023-08-09 20:00:00     0.000000     0.000000     0.000000  0.0  0.0
2023-08-09 21:00:00     0.000000     0.000000     0.000000  0.0  0.0
2023-08-09 22:00:00     0.000000     0.000000     0.000000  0.0  0.0

[14605 rows x 5 columns]

In [127]:
df_hora_media = df_filtered[['RadiacaoGlobal','TempAr', 'TempModulo','VelocidadeVento']]
df_hora_media = df_hora_media.resample('H').mean()
df_hora_media = df_hora_media.fillna(0)

In [128]:
df_hora = pd.concat([df_hora_soma,df_hora_media], axis = 1)
df_hora

yB           yC           yD   yE   yF   
E3TimeStamp                                                            
2021-12-09 10:00:00     0.000000     0.000000     0.000000  0.0  0.0  \
2021-12-09 11:00:00   496.200000   486.650000   395.000000  0.0  0.0   
2021-12-09 12:00:00    70.000000    71.800000    71.000000  0.0  0.0   
2021-12-09 13:00:00    19.000000    86.000000    89.000000  0.0  0.0   
2021-12-09 14:00:00  1433.030928  1540.227835  1601.291753  0.0  0.0   
...                          ...          ...          ...  ...  ...   
2023-08-09 18:00:00     2.100000     2.200000     2.300000  2.2  2.4   
2023-08-09 19:00:00     0.000000     0.000000     0.000000  0.0  0.0   
2023-08-09 20:00:00     0.000000     0.000000     0.000000  0.0  0.0   
2023-08-09 21:00:00     0.000000     0.000000     0.000000  0.0  0.0   
2023-08-09 22:00:00     0.000000     0.000000     0.000000  0.0  0.0   

                     RadiacaoGlobal     TempAr  TempModulo  VelocidadeVento  
E3TimeStamp                                                                  
2021-12-09 10:00:00        0.000000   0.000000    0.000000         0.000000  
2021-12-09 11:00:00      237.593750   6.239583   13.682292         0.406250  
2021-12-09 12:00:00      441.411392  11.468354   25.405063         0.949367  
2021-12-09 13:00:00      474.673913  13.862319   21.539855         0.905797  
2021-12-09 14:00:00      492.442478  16.805310   32.309735         1.274336  
...                             ...        ...         ...              ...  
2023-08-09 18:00:00       -1.833333  24.383333   22.200000         0.666667  
2023-08-09 19:00:00       -7.033333  22.566667   19.750000         0.483333  
2023-08-09 20:00:00       -4.483333  21.100000   18.066667         0.400000  
2023-08-09 21:00:00       -4.250000  20.800000   18.066667         0.900000  
2023-08-09 22:00:00       -1.550000  21.000000   18.600000         2.850000  

[14605 rows x 9 columns]

In [130]:
df_corr = df_hora.corr()

fig = px.imshow(df_corr, text_auto=True, aspect="auto")
fig.show()

## Analise resultados com correlação e tabela de valores min, max, etc

In [129]:
try:
  df_hora = df_hora.set_index('E3TimeStamp')
except:
  pass

df_descricao = pd.DataFrame()

df_descricao['No_None_Values_Count'] = round(df_hora.apply(lambda x: x.count()),2)
df_descricao['None_Values_Count'] = round(df_hora.apply(lambda x: x.isnull().sum()),2)
df_descricao['Zeroes_Values_Count'] = round(df_hora.apply(lambda x: (x == 0).sum()),2)
df_descricao['Min_Values'] = round(df_hora.apply(lambda x: x.min()),2)
df_descricao['Max_Values'] = round(df_hora.apply(lambda x: x.max()),2)
df_descricao['Mean_Values'] = round(df_hora.apply(lambda x: x.mean()),2)
df_descricao['Std_Values'] = round(df_hora.apply(lambda x: x.std()),2)
df_descricao['Sum of Values'] = round(df_hora.apply(lambda x: x.sum()),0)
df_descricao['Min_Date'] = df_hora.index.min()
df_descricao['Max_Date'] = df_hora.index.max()
df_descricao

No_None_Values_Count  None_Values_Count  Zeroes_Values_Count   
yB                              14605                  0                 8130  \
yC                              14605                  0                 8200   
yD                              14605                  0                 8510   
yE                              14605                  0                 8080   
yF                              14605                  0                 8063   
RadiacaoGlobal                  14605                  0                 1826   
TempAr                          14605                  0                 1806   
TempModulo                      14605                  0                 1806   
VelocidadeVento                 14605                  0                 1971   

                 Min_Values  Max_Values  Mean_Values  Std_Values   
yB                     0.00     1433.03       203.49      322.09  \
yC                     0.00     1540.23       197.85      317.00   
yD                     0.00     1601.29       186.99      311.82   
yE                     0.00     1008.10       200.46      318.80   
yF                     0.00     1008.20       205.25      324.06   
RadiacaoGlobal       -11.14     1189.65       189.60      294.84   
TempAr                 0.00       38.78        20.65        9.30   
TempModulo             0.00       68.37        24.40       15.47   
VelocidadeVento      -10.00        5.51         0.43        3.84   

                 Sum of Values            Min_Date            Max_Date  
yB                   2971977.0 2021-12-09 10:00:00 2023-08-09 22:00:00  
yC                   2889621.0 2021-12-09 10:00:00 2023-08-09 22:00:00  
yD                   2730929.0 2021-12-09 10:00:00 2023-08-09 22:00:00  
yE                   2927693.0 2021-12-09 10:00:00 2023-08-09 22:00:00  
yF                   2997650.0 2021-12-09 10:00:00 2023-08-09 22:00:00  
RadiacaoGlobal       2769102.0 2021-12-09 10:00:00 2023-08-09 22:00:00  
TempAr                301521.0 2021-12-09 10:00:00 2023-08-09 22:00:00  
TempModulo            356310.0 2021-12-09 10:00:00 2023-08-09 22:00:00  
VelocidadeVento         6252.0 2021-12-09 10:00:00 2023-08-09 22:00:00

# Weather Data

In [131]:
path = 'C:/Users/EMC/Documents/doutorado/doctorade/data/loanda/weather_data/loanda_weather_curated.json'
with open(path, "r") as json_file:
# Load the JSON data into a Python object.
    json_data = json.load(json_file)
    df_weather = pd.DataFrame.from_dict(json_data)

df_time = df_weather['time_in_iso8601']

df_float = df_weather[[
       'temperature_2m_in_°C', 'relativehumidity_2m_in_%',
       'precipitation_in_mm', 'weathercode_in_wmo code_x', 'cloudcover_in_%',
       'cloudcover_low_in_%', 'cloudcover_mid_in_%', 'cloudcover_high_in_%',
       'windspeed_10m_in_km/h', 'is_day_in_', 'shortwave_radiation_in_W/m²',
       'direct_radiation_in_W/m²', 'diffuse_radiation_in_W/m²',
       'direct_normal_irradiance_in_W/m²', 'terrestrial_radiation_in_W/m²',
       'shortwave_radiation_instant_in_W/m²',
       'direct_radiation_instant_in_W/m²', 'diffuse_radiation_instant_in_W/m²',
       'direct_normal_irradiance_instant_in_W/m²',
       'terrestrial_radiation_instant_in_W/m²',
       'weathercode_in_wmo code_y', 'temperature_2m_max_in_°C',
       'temperature_2m_min_in_°C', 'temperature_2m_mean_in_°C',
       'apparent_temperature_max_in_°C', 'apparent_temperature_min_in_°C',
       'apparent_temperature_mean_in_°C', 'precipitation_sum_in_mm', 'rain_sum_in_mm',
       'precipitation_hours_in_h', 'windspeed_10m_max_in_km/h',
       'windgusts_10m_max_in_km/h', 'winddirection_10m_dominant_in_°',
       'shortwave_radiation_sum_in_MJ/m²', 'et0_fao_evapotranspiration_in_mm',
       'time_of_sunlight_in_iso8601']].astype(float)

df_weather = pd.concat([df_time,df_float], axis = 1)

df_weather = df_weather.sort_values(by='time_in_iso8601')

# Concat weather e generation data

In [132]:
df_hora = df_hora.reset_index()
df_hora['time_join_generation'] = df_hora['E3TimeStamp'].dt.date.astype(str) +' '+ df_hora['E3TimeStamp'].dt.hour.astype(str)
df_weather['time_in_iso8601'] = pd.to_datetime(df_weather['time_in_iso8601'], format='ISO8601')
df_weather['time_join_generation'] = df_weather['time_in_iso8601'].dt.date.astype(str) +' '+ df_weather['time_in_iso8601'].dt.hour.astype(str)

In [151]:
df_hora_all = df_hora.merge(df_weather,how='left',on = 'time_join_generation')
try:
    del df_hora_all['time_in_iso8601']
except:
    pass
try:
    del df_hora_all['time_join_generation']
except:
    pass
df_hora_all = df_hora_all.set_index("E3TimeStamp")


In [180]:
df_hora_all[df_hora_all['cloudcover_in_%'] > 90]

yB    yC    yD    yE    yF  RadiacaoGlobal  TempAr   
E3TimeStamp                                                                 
2021-12-13 22:00:00   0.0   0.0   0.0   0.0   0.0       -3.183333   25.00  \
2021-12-13 23:00:00   0.0   0.0   0.0   0.0   0.0       -2.950000   25.00   
2021-12-14 00:00:00   0.0   0.0   0.0   0.0   0.0       -3.500000   24.00   
2021-12-14 05:00:00   6.4   6.6   6.3   6.6   6.7        4.350000   24.00   
2021-12-14 06:00:00  61.6  61.0  61.5  61.9  60.6       53.300000   24.05   
...                   ...   ...   ...   ...   ...             ...     ...   
2023-07-29 17:00:00   0.0   0.0   0.0   0.0   0.0        0.000000    0.00   
2023-07-29 18:00:00   0.0   0.0   0.0   0.0   0.0        0.000000    0.00   
2023-07-29 19:00:00   0.0   0.0   0.0   0.0   0.0        0.000000    0.00   
2023-07-29 20:00:00   0.0   0.0   0.0   0.0   0.0        0.000000    0.00   
2023-07-29 21:00:00   0.0   0.0   0.0   0.0   0.0        0.000000    0.00   

                     TempModulo  VelocidadeVento  temperature_2m_in_°C  ...   
E3TimeStamp                                                             ...   
2021-12-13 22:00:00   23.116667         0.300000                  26.8  ...  \
2021-12-13 23:00:00   23.416667         0.250000                  26.2  ...   
2021-12-14 00:00:00   23.133333         0.850000                  25.5  ...   
2021-12-14 05:00:00   23.483333         0.883333                  22.6  ...   
2021-12-14 06:00:00   24.966667         1.516667                  22.6  ...   
...                         ...              ...                   ...  ...   
2023-07-29 17:00:00    0.000000         0.000000                  23.3  ...   
2023-07-29 18:00:00    0.000000         0.000000                  22.7  ...   
2023-07-29 19:00:00    0.000000         0.000000                  22.0  ...   
2023-07-29 20:00:00    0.000000         0.000000                  21.3  ...   
2023-07-29 21:00:00    0.000000         0.000000                  21.0  ...   

                     apparent_temperature_mean_in_°C  precipitation_sum_in_mm   
E3TimeStamp                                                                     
2021-12-13 22:00:00                             30.6                      0.0  \
2021-12-13 23:00:00                             30.6                      0.0   
2021-12-14 00:00:00                             29.9                      8.6   
2021-12-14 05:00:00                             29.9                      8.6   
2021-12-14 06:00:00                             29.9                      8.6   
...                                              ...                      ...   
2023-07-29 17:00:00                             21.2                      0.0   
2023-07-29 18:00:00                             21.2                      0.0   
2023-07-29 19:00:00                             21.2                      0.0   
2023-07-29 20:00:00                             21.2                      0.0   
2023-07-29 21:00:00                             21.2                      0.0   

                     rain_sum_in_mm  precipitation_hours_in_h   
E3TimeStamp                                                     
2021-12-13 22:00:00             0.0                       0.0  \
2021-12-13 23:00:00             0.0                       0.0   
2021-12-14 00:00:00             8.6                      18.0   
2021-12-14 05:00:00             8.6                      18.0   
2021-12-14 06:00:00             8.6                      18.0   
...                             ...                       ...   
2023-07-29 17:00:00             0.0                       0.0   
2023-07-29 18:00:00             0.0                       0.0   
2023-07-29 19:00:00             0.0                       0.0   
2023-07-29 20:00:00             0.0                       0.0   
2023-07-29 21:00:00             0.0                       0.0   

                     windspeed_10m_max_in_km/h  windgusts_10m_max_in_km/h   
E3TimeStamp     

In [156]:
df_corr = df_hora_all.corr()

In [173]:
df_corr.yB.sort_values()

relativehumidity_2m_in_%                   -0.348466
cloudcover_mid_in_%                        -0.128932
cloudcover_high_in_%                       -0.125020
precipitation_hours_in_h                   -0.109124
precipitation_sum_in_mm                    -0.098126
rain_sum_in_mm                             -0.098126
cloudcover_in_%                            -0.080739
weathercode_in_wmo code_y                  -0.054488
precipitation_in_mm                        -0.045192
windgusts_10m_max_in_km/h                  -0.018751
windspeed_10m_max_in_km/h                  -0.013998
weathercode_in_wmo code_x                  -0.005838
cloudcover_low_in_%                         0.010610
winddirection_10m_dominant_in_°             0.020030
apparent_temperature_min_in_°C              0.061281
temperature_2m_min_in_°C                    0.071677
apparent_temperature_mean_in_°C             0.096935
temperature_2m_mean_in_°C                   0.116408
apparent_temperature_max_in_°C              0.

# EDA

In [446]:
zeros_and_nulls = pd.concat([round((df == 0).sum()/len(df)*100,2),round(df.isna().sum()/len(df)*100,2)], axis = 1)
zeros_and_nulls.rename(columns={0: '% Zeros', 1: '% Nulls'}).sort_values(by = '% Nulls', ascending=False).head(30)

% Zeros  % Nulls
TempAr                                       0.63    10.48
TempModulo                                   0.63    10.48
VelocidadeVento                              2.04    10.48
E3TimeStamp                                  0.00     0.00
apparent_temperature_min_in_°C               0.00     0.00
direct_radiation_instant_in_W/m²            52.19     0.00
diffuse_radiation_instant_in_W/m²           50.48     0.00
direct_normal_irradiance_instant_in_W/m²    52.19     0.00
terrestrial_radiation_instant_in_W/m²       49.99     0.00
weathercode_in_wmo code_y                   16.99     0.00
temperature_2m_max_in_°C                     0.00     0.00
temperature_2m_min_in_°C                     0.00     0.00
temperature_2m_mean_in_°C                    0.00     0.00
apparent_temperature_max_in_°C               0.00     0.00
precipitation_sum_in_mm                     48.34     0.00
apparent_temperature_mean_in_°C              0.00     0.00
terrestrial_radiation_in_W/m²               46.37     0.00
rain_sum_in_mm                              48.34     0.00
precipitation_hours_in_h                    48.34     0.00
windspeed_10m_max_in_km/h                    0.00     0.00
windgusts_10m_max_in_km/h                    0.00     0.00
winddirection_10m_dominant_in_°              0.41     0.00
shortwave_radiation_sum_in_MJ/m²             0.00     0.00
et0_fao_evapotranspiration_in_mm             0.00     0.00
shortwave_radiation_instant_in_W/m²         50.47     0.00
diffuse_radiation_in_W/m²                   46.88     0.00
direct_normal_irradiance_in_W/m²            49.70     0.00
RadiacaoGlobal                              11.23     0.00
yB                                          58.62     0.00
yC                                          59.11     0.00

In [459]:
try:
  df = df.set_index('E3TimeStamp')
except:
  pass
try:
  del df['time_join_generation']
except:
  pass
try:
  del df['time_in_iso8601']
except:
  pass


df_descricao = pd.DataFrame()

df_descricao['No_None_Values_Count'] = round(df.apply(lambda x: x.count()),2)
df_descricao['None_Values_Count'] = round(df.apply(lambda x: x.isnull().sum()),2)
df_descricao['Zeroes_Values_Count'] = round(df.apply(lambda x: (x == 0).sum()),2)
df_descricao['Min_Values'] = round(df.apply(lambda x: x.min()),2)
df_descricao['Max_Values'] = round(df.apply(lambda x: x.max()),2)
df_descricao['Mean_Values'] = round(df.apply(lambda x: x.mean()),2)
df_descricao['Std_Values'] = round(df.apply(lambda x: x.std()),2)
df_descricao['Sum of Values'] = round(df.apply(lambda x: x.sum()),0)
df_descricao['Min_Date'] = df.index.min()
df_descricao['Max_Date'] = df.index.max()
df_descricao

No_None_Values_Count   
RadiacaoGlobal                                           17653  \
yB                                                       17653   
yC                                                       17653   
yD                                                       17653   
yE                                                       17653   
yF                                                       17653   
TempAr                                                   15803   
TempModulo                                               15803   
VelocidadeVento                                          15803   
temperature_2m_in_°C                                     17653   
relativehumidity_2m_in_%                                 17653   
precipitation_in_mm                                      17653   
weathercode_in_wmo code_x                                17653   
cloudcover_in_%                                          17653   
cloudcover_low_in_%                                      17653   
cloudcover_mid_in_%                                      17653   
cloudcover_high_in_%                                     17653   
windspeed_10m_in_km/h                                    17653   
is_day_in_                                               17653   
shortwave_radiation_in_W/m²                              17653   
direct_radiation_in_W/m²                                 17653   
diffuse_radiation_in_W/m²                                17653   
direct_normal_irradiance_in_W/m²                         17653   
terrestrial_radiation_in_W/m²                            17653   
shortwave_radiation_instant_in_W/m²                      17653   
direct_radiation_instant_in_W/m²                         17653   
diffuse_radiation_instant_in_W/m²                        17653   
direct_normal_irradiance_instant_in_W/m²                 17653   
terrestrial_radiation_instant_in_W/m²                    17653   
weathercode_in_wmo code_y                                17653   
temperature_2m_max_in_°C                                 17653   
temperature_2m_min_in_°C                                 17653   
temperature_2m_mean_in_°C                                17653   
apparent_temperature_max_in_°C                           17653   
apparent_temperature_min_in_°C                           17653   
apparent_temperature_mean_in_°C                          17653   
precipitation_sum_in_mm                                  17653   
rain_sum_in_mm                                           17653   
precipitation_hours_in_h                                 17653   
windspeed_10m_max_in_km/h                                17653   
windgusts_10m_max_in_km/h                                17653   
winddirection_10m_dominant_in_°                          17653   
shortwave_radiation_sum_in_MJ/m²                         17653   
et0_fao_evapotranspiration_in_mm                         17653   
time_of_sunlight_in_iso8601                              17653   

                                          None_Values_Count   
RadiacaoGlobal                                            0  \
yB                                                        0   
yC                                                        0   
yD                                                        0   
yE                                                        0   
yF                                                        0   
TempAr                                                 1850   
TempModulo                                             1850   
VelocidadeVento                                        1850   
temperature_2m_in_°C                                      0   
relativehumidity_2m_in_%                                  0   
precipitation_in_mm                                       0   
weathercode_in_wmo code_x                                 0   
cloudcover_in_%                                           0   
cloudcover_low_in_%                                       0 

In [477]:
df_generation[(pd.to_datetime(df_generation.E3TimeStamp, format = 'mixed') >= '2021-12-09') & (pd.to_datetime(df_generation.E3TimeStamp, format = 'mixed') <= '2021-12-09 18:00:00')]

E3TimeStamp PotenciaAtivaTotal   
63416   2021-12-09 09:34:42.630000000               2883  \
63417   2021-12-09 09:35:42.653000000               2889   
63418   2021-12-09 09:36:42.640000000               2897   
63419   2021-12-09 09:37:42.650000000               2904   
63420   2021-12-09 09:38:42.660000000               2914   
...                               ...                ...   
192933  2021-12-09 17:55:24.557000000                436   
192934  2021-12-09 17:56:24.563000000                420   
192935  2021-12-09 17:57:24.560000000                405   
192936  2021-12-09 17:58:24.563000000                390   
192937  2021-12-09 17:59:24.547000000                376   

       EnergiaTotal_DataLogger EnergiaDiaria_DataLogger RadiacaoGlobal TempAr   
63416                  1992737                     5207          901.0   25.0  \
63417                  1992786                     5257          903.0   26.0   
63418                  1992835                     5304          906.0   26.0   
63419                  1992883                     5353          915.0   26.0   
63420                  1992930                     5401          917.0   26.0   
...                        ...                      ...            ...    ...   
192933                 2017072                    28567          186.0   31.0   
192934                 2017079                    28574          182.0   31.0   
192935                 2017085                    28580          178.0   31.0   
192936                 2017092                    28587          173.0   31.0   
192937                 2017098                    28593          169.0   30.0   

       TempModulo VelocidadeVento EnergiaTotal_LoteB EnergiaDiaria_LoteB  ...   
63416        48.0             2.0           949063.2              1756.0  ...  \
63417        49.0             3.0           949079.8              1772.3  ...   
63418        49.0             2.0           949095.8              1788.4  ...   
63419        50.0             3.0           949111.6              1803.8  ...   
63420        50.0             4.0           949126.8              1820.0  ...   
...           ...             ...                ...                 ...  ...   
192933       32.0             1.0           953885.3              6577.9  ...   
192934       31.0             1.0           953886.6              6579.2  ...   
192935       31.0             1.0           953887.8              6580.4  ...   
192936       31.0             2.0           953889.0              6581.6  ...   
192937       31.0             1.0           953890.2              6582.8  ...   

       EnergiaReativa_LoteC EnergiaTotal_LoteD EnergiaDiaria_LoteD   
63416                 8.282           206490.6              1725.4  \
63417                10.492           206506.9              1741.5   
63418                -3.314           206523.0              1757.5   
63419                 5.247           206539.1              1773.8   
63420                  8.82           206555.2              1790.0   
...                     ...                ...                 ...   
192933                2.931           211501.3              6735.9   
192934                3.151           211502.9              6737.5   
192935                2.919           211504.4              6739.0   
192936                2.882           211505.8              6740.4   
192937                2.896           211507.1              6741.7   

       EnergiaReativa_LoteD EnergiaTotal_LoteE EnergiaDiaria_LoteE   
63416                 9.346                nan                 nan  \
63417                11.178                nan                 nan   
63418                -4.719                nan                 nan   
63419                 5.573                nan                 nan   
63420                 9.826                nan                 nan   
...                     ...                ...                 ...   
192933                3.587 

In [476]:
pd.to_datetime(df_generation.E3TimeStamp, format = 'mixed')

0        2021-08-17 07:42:20.090
1        2021-08-17 07:43:20.043
2        2021-08-17 07:44:20.037
3        2021-08-17 07:45:20.127
4        2021-08-17 07:46:20.027
                   ...          
949868   2023-08-09 22:16:10.357
949869   2023-08-09 22:17:10.407
949870   2023-08-09 22:18:10.380
949871   2023-08-09 22:19:10.373
949872   2023-08-09 22:20:10.317
Name: E3TimeStamp, Length: 949873, dtype: datetime64[ns]